In [74]:
from ast import literal_eval
from os import listdir
from os.path import isfile, join
from scipy.sparse import csr_matrix, load_npz, save_npz
from tqdm import tqdm
import statistics as stats
import seaborn as sns
import datetime
import json
import numpy as np
import pandas as pd
import time
import yaml
import scipy.sparse as sparse

## Dataset files 

In [2]:
#reviewJson = "..\\data\\Export_CleanedReview.json"
reviewJsonWithClosedRes = "..\\data\\Export_CleanedReviewWithClosedRes.json"

# with open(reviewJson, encoding = 'utf-8') as json_file:
#     data = json_file.readlines()
#     data = list(map(json.loads, data))

#This appeared to be a neasted list, just use data[0] to read
# df_review = pd.DataFrame(data[0])

## Load Data
Select top frenquent user and top frequenty restaurants that had at least 1 review >= 4 stars (Kickking out users that gave all  reviews <=3 and restaurants that never got start >= 4 stars)

In [3]:
def get_yelp_df(path = 'data/', filename = 'Export_CleanedReview.json', sampling=False, top_user_num=6100, top_item_num=4000):
    """
    Get the pandas dataframe
    Sampling only the top users/items by density 
    Implicit representation applies
    """
    with open(filename,'r') as f:
        data = f.readlines()
        data = list(map(json.loads, data))
    
    data = data[0]
    #Get all the data from the data file
    df = pd.DataFrame(data)
    
    df.rename(columns={'stars': 'review_stars', 'text': 'review_text', 'cool': 'review_cool',
                       'funny': 'review_funny', 'useful': 'review_useful'},
              inplace=True)

    df['business_num_id'] = df.business_id.astype('category').\
        cat.rename_categories(range(0, df.business_id.nunique()))
    df['business_num_id'] = df['business_num_id'].astype('int')

    df['user_num_id'] = df.user_id.astype('category').\
    cat.rename_categories(range(0, df.user_id.nunique()))
    df['user_num_id'] = df['user_num_id'].astype('int')

    df['timestamp'] = df['date'].apply(date_to_timestamp)

    if sampling:
        df = filter_yelp_df(df, top_user_num=top_user_num, top_item_num=top_item_num)
        # Refresh num id
        df['business_num_id'] = df.business_id.astype('category').\
        cat.rename_categories(range(0, df.business_id.nunique()))
        df['business_num_id'] = df['business_num_id'].astype('int')
        
        df['user_num_id'] = df.user_id.astype('category').\
        cat.rename_categories(range(0, df.user_id.nunique()))
        df['user_num_id'] = df['user_num_id'].astype('int')
#     drop_list = ['date','review_id','review_funny','review_cool','review_useful']
#     df = df.drop(drop_list, axis=1)

    df = df.reset_index(drop = True)

    return df 

def filter_yelp_df(df, top_user_num=6100, top_item_num=4000):
    #Getting the reviews where starts are above 3
    df_implicit = df[df['review_stars']>3]
    frequent_user_id = df_implicit['user_num_id'].value_counts().head(top_user_num).index.values
    frequent_item_id = df_implicit['business_num_id'].value_counts().head(top_item_num).index.values
    return df.loc[(df['user_num_id'].isin(frequent_user_id)) & (df['business_num_id'].isin(frequent_item_id))]

def date_to_timestamp(date):
    dt = datetime.datetime.strptime(date, '%Y-%m-%d')
    return time.mktime(dt.timetuple())

def df_to_sparse(df, row_name='userId', col_name='movieId', value_name='rating',
                 shape=None):
    rows = df[row_name]
    cols = df[col_name]
    if value_name is not None:
        values = df[value_name]
    else:
        values = [1]*len(rows)

    return csr_matrix((values, (rows, cols)), shape=shape)

## Get rating-UI and timestamp-UI matrix from original df

In [18]:
def get_rating_timestamp_matrix(df, sampling=False, top_user_num=6100, top_item_num=4000):
    """
    """
    #make the df implicit with top frenquent users and 
    #no need to sample anymore if df was sampled before 
    if sampling:
        df = filter_yelp_df(df, top_user_num=top_user_num, top_item_num=top_item_num)

    rating_matrix = df_to_sparse(df, row_name='user_num_id',
                                 col_name='business_num_id',
                                 value_name='review_stars',
                                 shape=None)
    
    #Have same dimension and data entries with rating_matrix, except that the review stars are - user avg
    ratingWuserAvg_matrix = df_to_sparse(df, row_name='user_num_id',
                                 col_name='business_num_id',
                                 value_name='reviewStars_userAvg',
                                 shape=None)
    
    timestamp_matrix = df_to_sparse(df, row_name='user_num_id',
                                    col_name='business_num_id',
                                    value_name='timestamp',
                                    shape=None)
    

    return rating_matrix, ratingWuserAvg_matrix, timestamp_matrix

## Time ordered split 

In [149]:
def time_ordered_split(rating_matrix, ratingWuserAvg_matrix, timestamp_matrix, ratio=[0.5, 0.2, 0.3],
                       implicit=True, remove_empty=False, threshold=3,
                       sampling=False, sampling_ratio=0.1):
    """
    Split the data to train,valid,test by time
    ratio:  train:valid:test
    threshold: for implicit representation
    """
    if implicit:
        temp_rating_matrix = sparse.csr_matrix(rating_matrix.shape)
        temp_rating_matrix[(rating_matrix > threshold).nonzero()] = 1
        rating_matrix = temp_rating_matrix
        timestamp_matrix = timestamp_matrix.multiply(rating_matrix)
        #ratingWuserAvg_matrix = ratingWuserAvg_matrix.multiply(rating_matrix)

    nonzero_index = None

    #Default false, not removing empty columns and rows
    #Should not have this case, since users should have at least 1 record of 4,5 
    #And restuarant should have at least 1 record of 4,5 
    if remove_empty:
        # Remove empty columns. record original item index
        nonzero_index = np.unique(rating_matrix.nonzero()[1])
        rating_matrix = rating_matrix[:, nonzero_index]
        timestamp_matrix = timestamp_matrix[:, nonzero_index]
        ratingWuserAvg_matrix = ratingWuserAvg_matrix[:, nonzero_index]

        # Remove empty rows. record original user index
        nonzero_rows = np.unique(rating_matrix.nonzero()[0])
        rating_matrix = rating_matrix[nonzero_rows]
        timestamp_matrix = timestamp_matrix[nonzero_rows]
        ratingWuserAvg_matrix = ratingWuserAvg_matrix[nonzero_rows]

    user_num, item_num = rating_matrix.shape

    rtrain = []
    rtrain_userAvg = []
    rtime = []
    rvalid = []
    rvalid_userAvg = []
    rtest = []
    rtest_userAvg = []
    # Get the index list corresponding to item for train,valid,test
    item_idx_train = []
    item_idx_valid = []
    item_idx_test = []
    
    for i in tqdm(range(user_num)):
        #Get the non_zero indexs, restuarants where the user visited/liked if implicit 
        item_indexes = rating_matrix[i].nonzero()[1]
        
        #Get the data for the user
        data = rating_matrix[i].data
        
        #Get time stamp value 
        timestamp = timestamp_matrix[i].data
        
        #Get review stars with user avg data 
        if implicit == False:
            dataWuserAvg = ratingWuserAvg_matrix[i].data
        
        #Non zero reviews for this user
        num_nonzeros = len(item_indexes)
        
        #If the user has at least one review
        if num_nonzeros >= 1:
            #Get number of test and valid data 
            #train is 30%
            num_test = int(num_nonzeros * ratio[2])
            #validate is 50%
            num_valid = int(num_nonzeros * (ratio[1] + ratio[2]))

            valid_offset = num_nonzeros - num_valid
            test_offset = num_nonzeros - num_test

            #Sort the timestamp for each review for the user
            argsort = np.argsort(timestamp)
            
            #Sort the reviews for the user according to the time stamp 
            data = data[argsort]
            
            #Sort the review with user avg accoridng to the time stamp
            if implicit == False:
                dataWuserAvg = dataWuserAvg[argsort]
            
            #Non-zero review index sort according to time
            item_indexes = item_indexes[argsort]
            
            #list of ratings, num of valid_offset index, index where there's non-zeros
            rtrain.append([data[:valid_offset], np.full(valid_offset, i), item_indexes[:valid_offset]])
            
            if implicit == False:
                #Changing valid set to binary
                count=valid_offset
                for eachData in data[valid_offset:test_offset]:
                    #if rating-avgRating > 0 then like
                    if eachData >= 4:
                        data[count] = 1
                    else:
                        data[count] = 0
                    count += 1
                
            #50%-70%
            rvalid.append([data[valid_offset:test_offset], np.full(test_offset - valid_offset, i),
                           item_indexes[valid_offset:test_offset]])
            #remaining 30%
            rtest.append([data[test_offset:], np.full(num_test, i), item_indexes[test_offset:]])
            
            if implicit == False:
                #Now for the rating matrix that considers user average rating
                #list of ratings, num of valid_offset index, index where there's non-zeros
                rtrain_userAvg.append([dataWuserAvg[:valid_offset], np.full(valid_offset, i), item_indexes[:valid_offset]])
                #50%-70%

                #Changing valid set to binary
                count=valid_offset
                for eachData in dataWuserAvg[valid_offset:test_offset]:
                    #if rating-avgRating > 0 then like
                    if eachData > 0:
                        dataWuserAvg[count] = 1
                    else:
                        dataWuserAvg[count] = 0
                    count += 1

                rvalid_userAvg.append([dataWuserAvg[valid_offset:test_offset], np.full(test_offset - valid_offset, i),
                               item_indexes[valid_offset:test_offset]])

                #Change test set to binary even we don't use it
                countTest = test_offset
                for eachData in dataWuserAvg[test_offset:]:
                    #if rating-avgRating > 0 then like
                    if eachData > 0:
                        dataWuserAvg[count] = 1
                    else:
                        dataWuserAvg[count] = 0
                    count += 1


                #remaining 30%
                rtest_userAvg.append([dataWuserAvg[test_offset:], np.full(num_test, i), item_indexes[test_offset:]])
                
            item_idx_train.append(item_indexes[:valid_offset])
            
#             item_idx_valid.append(item_indexes[valid_offset:test_offset])
#             item_idx_test.append(item_indexes[test_offset:])
        else:
            item_idx_train.append([])
#             item_idx_valid.append([])
#             item_idx_test.append([])
    
    rtrain = np.array(rtrain)
    rvalid = np.array(rvalid)
    rtest = np.array(rtest)
    if implicit == False:
        rtrain_userAvg = np.array(rtrain_userAvg)
        rvalid_userAvg = np.array(rvalid_userAvg)
        rtest_userAvg = np.array(rtest_userAvg)

    #take non-zeros values, row index, and column (non-zero) index and store into sparse matrix
    rtrain = sparse.csr_matrix((np.hstack(rtrain[:, 0]), (np.hstack(rtrain[:, 1]), np.hstack(rtrain[:, 2]))),
                               shape=rating_matrix.shape, dtype=np.float32)
    rvalid = sparse.csr_matrix((np.hstack(rvalid[:, 0]), (np.hstack(rvalid[:, 1]), np.hstack(rvalid[:, 2]))),
                               shape=rating_matrix.shape, dtype=np.float32)
    rtest = sparse.csr_matrix((np.hstack(rtest[:, 0]), (np.hstack(rtest[:, 1]), np.hstack(rtest[:, 2]))),
                              shape=rating_matrix.shape, dtype=np.float32)
    
    if implicit == False:
        rtrain_userAvg = sparse.csr_matrix((np.hstack(rtrain_userAvg[:, 0]), (np.hstack(rtrain_userAvg[:, 1]), np.hstack(rtrain_userAvg[:, 2]))),
                                   shape=rating_matrix.shape, dtype=np.float32)
        rvalid_userAvg = sparse.csr_matrix((np.hstack(rvalid_userAvg[:, 0]), (np.hstack(rvalid_userAvg[:, 1]), np.hstack(rvalid_userAvg[:, 2]))),
                                   shape=rating_matrix.shape, dtype=np.float32)
        rtest_userAvg = sparse.csr_matrix((np.hstack(rtest_userAvg[:, 0]), (np.hstack(rtest_userAvg[:, 1]), np.hstack(rtest_userAvg[:, 2]))),
                                  shape=rating_matrix.shape, dtype=np.float32)

    return rtrain, rvalid, rtest,rtrain_userAvg, rvalid_userAvg, rtest_userAvg, nonzero_index, timestamp_matrix, item_idx_train, item_idx_valid, item_idx_test

## Get df for training corpus

In [6]:
#Item idex matrix stores the reivews starts
#This function returns a list of index for the reviews included in training set 
def get_corpus_idx_list(df, item_idx_matrix):
    """
    Input: 
    df: total dataframe
    item_idx_matrix: train index list got from time_split 
    Output: row index in original dataframe for training data by time split
    """
    lst = []
    #For all the users: 5791
    for i in tqdm(range(len(item_idx_matrix))):
        
        #find row index where user_num_id is i
        a = df.index[df['user_num_id'] == i].tolist()
        
        #loop through the busienss id that the user i reviewed for in offvalid set 
        for item_idx in  item_idx_matrix[i]:
            
            #get the row index for reviews for business that the user liked in the train set
            b = df.index[df['business_num_id'] == item_idx].tolist()
            
            #Find the index for which this user liked, one user only rate a business once
            idx_to_add = list(set(a).intersection(b))
            
            if idx_to_add not in lst:
                lst.extend(idx_to_add)
    return lst

## Preprocess using Term Frequency - CounterVectorizer

In [7]:
#Stemming and Lemmatisation
from nltk.stem.porter import PorterStemmer
from nltk.stem.wordnet import WordNetLemmatizer
import re 
import nltk
from nltk.corpus import stopwords
from nltk.stem.porter import PorterStemmer
from nltk.tokenize import RegexpTokenizer
# Get corpus and CountVector
from sklearn.feature_extraction.text import CountVectorizer
nltk.download('wordnet')
nltk.download('stopwords')
lem = WordNetLemmatizer()
stem = PorterStemmer()
stop_words = set(stopwords.words("english"))
new_words = ['not_the']
stop_words = stop_words.union(new_words)

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\shenti10\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!
[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\shenti10\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [8]:
from tqdm import tqdm

#Should 'because' added?
def preprocess(df, reset_list = [',','.','?',';','however','but']):
    corpus = []
    for i in tqdm(range(df.shape[0])):
        text = df['review_text'][i]
        change_flg = 0
        #Convert to lowercase
        text = text.lower()
        
        ##Convert to list from string, loop through the review text
        text = text.split()
        
        #any sentence that encounters a not, the folloing words will become not phrase until hit the sentence end
        for j in range(len(text)):
            #Make the not_ hack
            if text[j] == 'not':
                change_flg = 1
#                 print 'changes is made after ', i
                continue
            #if was 1 was round and not hit a 'not' in this round
            if change_flg == 1 and any(reset in text[j] for reset in reset_list):
                text[j] = 'not_' + text[j]
                change_flg = 0
#                 print 'reset at ', i
            if change_flg == 1:
                text[j] = 'not_' + text[j]
        
        #Convert back to string
        text = " ".join(text)
        
        #Remove punctuations
#       text = re.sub('[^a-zA-Z]', ' ', text)
        
        #remove tags
        text=re.sub("&lt;/?.*?&gt;"," &lt;&gt; ",text)
        
        # remove special characters and digits
        text=re.sub("(\\d|\\W)+"," ",text)
        
        ##Convert to list from string
        text = text.split()
        
        ##Stemming
        ps=PorterStemmer()
        
        #Lemmatisation
        lem = WordNetLemmatizer()
        text = [lem.lemmatize(word) for word in text if not word in  
                stop_words] 
        text = " ".join(text)
        corpus.append(text)
    return corpus

## All Model

In [19]:
from sklearn.metrics.pairwise import cosine_similarity
def train(matrix_train):
    similarity = cosine_similarity(X=matrix_train, Y=None, dense_output=True)
    return similarity

def get_I_K(df, X, row_name = 'business_num_id', binary = True, shape = (121994,6000)):
    """
    get the item-keyphrase matrix
    """
    rows = []
    cols = []
    vals = []
    #For each review history
    for i in tqdm(range(X.shape[0])):
        #Get the array of frequencies for document/review i 
        arr = X[i].toarray() 
        nonzero_element = arr.nonzero()[1]  # Get nonzero element in each line, keyphrase that appears index 
        length_of_nonzero = len(nonzero_element) #number of important keyphrase that appears
        
        # df[row_name][i] is the item idex
        #Get a list row index that indicates the document/review
        rows.extend(np.array([df[row_name][i]]*length_of_nonzero)) ## Item index
        #print(rows)
        
        #Get a list of column index indicating the key phrase that appears in i document/review
        cols.extend(nonzero_element) ## Keyword Index
        if binary:
            #Create a bunch of 1s
            vals.extend(np.array([1]*length_of_nonzero))
        else:
            #If not binary 
            vals.extend(arr[arr.nonzero()])    
    return csr_matrix((vals, (rows, cols)), shape=shape)


#Get a UI matrix if it's not item_similarity based or else IU
def predict(matrix_train, k, similarity, item_similarity_en = False):
    prediction_scores = []
    
    #inverse to IU matrix
    if item_similarity_en:
        matrix_train = matrix_train.transpose()
        
    #for each user or item, depends UI or IU 
    for user_index in tqdm(range(matrix_train.shape[0])):
        # Get user u's prediction scores for all items
        #Get prediction/similarity score for each user 1*num or user or num of items
        vector_u = similarity[user_index]

        # Get closest K neighbors excluding user u self
        #Decending accoding to similarity score, select top k
        similar_users = vector_u.argsort()[::-1][1:k+1]
        
        # Get neighbors similarity weights and ratings
        similar_users_weights = similarity[user_index][similar_users]
        
        #similar_users_weights_sum = np.sum(similar_users_weights)
        #print(similar_users_weights.shape)
        #shape: num of res * k
        similar_users_ratings = matrix_train[similar_users].toarray()
              
        prediction_scores_u = similar_users_ratings * similar_users_weights[:, np.newaxis]
        #print(prediction_scores_u)
        
        
        prediction_scores.append(np.sum(prediction_scores_u, axis=0))
        
    res = np.array(prediction_scores)
    
    if item_similarity_en:
        res = res.transpose()
    return res

#Get a UI matrix if it's not item_similarity based or else IU
def predictUU(matrix_train, k, similarity1, similarity2, similarity3, chooseWeigthMethod = 'max', weight1, weight2, weight3, item_similarity_en = False):
    prediction_scores = []
    
    #inverse to IU matrix
    if item_similarity_en:
        matrix_train = matrix_train.transpose()
        
    #for each user or item, depends UI or IU 
    for user_index in tqdm(range(matrix_train.shape[0])):
        # Get user u's prediction scores for all items
        #Get prediction/similarity score for each user 1*num or user or num of items
        vector_u = similarity[user_index]

        # Get closest K neighbors excluding user u self
        #Decending accoding to similarity score, select top k
        similar_users = vector_u.argsort()[::-1][1:k+1]
        
        # Get neighbors similarity weights and ratings
        similar_users_weights = similarity[user_index][similar_users]
        
        #similar_users_weights_sum = np.sum(similar_users_weights)
        #print(similar_users_weights.shape)
        #shape: num of res * k
        similar_users_ratings = matrix_train[similar_users].toarray()
              
        prediction_scores_u = similar_users_ratings * similar_users_weights[:, np.newaxis]
        #print(prediction_scores_u)
        
        
        prediction_scores.append(np.sum(prediction_scores_u, axis=0))
        
    res = np.array(prediction_scores)
    
    if item_similarity_en:
        res = res.transpose()
    return res


def predictII(matrix_train, k, similarity, item_similarity_en = False):
    prediction_scores = []
    
    #inverse to IU matrix
    if item_similarity_en:
        matrix_train = matrix_train.transpose()
        
    #for each user or item, depends UI or IU 
    for user_index in tqdm(range(matrix_train.shape[0])):
        # Get user u's prediction scores for all items
        #Get prediction/similarity score for each user 1*num or user or num of items
        vector_u = similarity[user_index]

        # Get closest K neighbors excluding user u self
        #Decending accoding to similarity score, select top k
        similar_users = vector_u.argsort()[::-1][1:k+1]
        
        # Get neighbors similarity weights and ratings
        similar_users_weights = similarity[user_index][similar_users]
        
        #similar_users_weights_sum = np.sum(similar_users_weights)
        #print(similar_users_weights.shape)
        #shape: num of res * k
        similar_users_ratings = matrix_train[similar_users].toarray()
              
        prediction_scores_u = similar_users_ratings * similar_users_weights[:, np.newaxis]
        #print(prediction_scores_u)
        
        
        prediction_scores.append(np.sum(prediction_scores_u, axis=0))
        
    res = np.array(prediction_scores)
    
    if item_similarity_en:
        res = res.transpose()
    return res



#Preidction score is UI or IU?
def prediction(prediction_score, topK, matrix_Train):

    prediction = []

    #for each user
    for user_index in tqdm(range(matrix_Train.shape[0])):
        
        #take the prediction scores for user 1 * num res
        vector_u = prediction_score[user_index]
        
        #The restuarant the user rated
        vector_train = matrix_Train[user_index]
        
        if len(vector_train.nonzero()[0]) > 0:
            vector_predict = sub_routine(vector_u, vector_train, topK=topK)
        else:
            vector_predict = np.zeros(topK, dtype=np.float32)

        prediction.append(vector_predict)

    return np.vstack(prediction)

#topK: the number of restuarants we are suggesting 
#if vector_train has number, then the user has visited
def sub_routine(vector_u, vector_train, topK=500):

    #index where non-zero
    train_index = vector_train.nonzero()[1]
    
    vector_u = vector_u
    
    #get topk + num rated res prediction score descending, top index 
    candidate_index = np.argpartition(-vector_u, topK+len(train_index))[:topK+len(train_index)]
    
    #sort top prediction score index in range topK+len(train_index) into vector_u`
    vector_u = candidate_index[vector_u[candidate_index].argsort()[::-1]]
    
    #deleted the rated res from the topk+train_index prediction score vector for user u 
    #Delete the user rated res index from the topk+numRated index
    vector_u = np.delete(vector_u, np.isin(vector_u, train_index).nonzero()[0])

    #so we only include the top K prediction score here
    return vector_u[:topK]

## Evaluation

In [10]:
def recallk(vector_true_dense, hits, **unused):
    hits = len(hits.nonzero()[0])
    return float(hits)/len(vector_true_dense)


def precisionk(vector_predict, hits, **unused):
    hits = len(hits.nonzero()[0])
    return float(hits)/len(vector_predict)


def average_precisionk(vector_predict, hits, **unused):
    precisions = np.cumsum(hits, dtype=np.float32)/range(1, len(vector_predict)+1)
    return np.mean(precisions)


def r_precision(vector_true_dense, vector_predict, **unused):
    vector_predict_short = vector_predict[:len(vector_true_dense)]
    hits = len(np.isin(vector_predict_short, vector_true_dense).nonzero()[0])
    return float(hits)/len(vector_true_dense)


def _dcg_support(size):
    arr = np.arange(1, size+1)+1
    return 1./np.log2(arr)


def ndcg(vector_true_dense, vector_predict, hits):
    idcg = np.sum(_dcg_support(len(vector_true_dense)))
    dcg_base = _dcg_support(len(vector_predict))
    dcg_base[np.logical_not(hits)] = 0
    dcg = np.sum(dcg_base)
    return dcg/idcg


def click(hits, **unused):
    first_hit = next((i for i, x in enumerate(hits) if x), None)
    if first_hit is None:
        return 5
    else:
        return first_hit/10


def evaluate(matrix_Predict, matrix_Test, metric_names =['R-Precision', 'NDCG', 'Precision', 'Recall', 'MAP'], atK = [5, 10, 15, 20, 50], analytical=False):
    """
    :param matrix_U: Latent representations of users, for LRecs it is RQ, for ALSs it is U
    :param matrix_V: Latent representations of items, for LRecs it is Q, for ALSs it is V
    :param matrix_Train: Rating matrix for training, features.
    :param matrix_Test: Rating matrix for evaluation, true labels.
    :param k: Top K retrieval
    :param metric_names: Evaluation metrics
    :return:
    """
    global_metrics = {
        #"R-Precision": r_precision,
        #"NDCG": ndcg,
        #"Clicks": click
    }

    local_metrics = {
        #"Precision": precisionk,
        #"Recall": recallk,
        "MAP": average_precisionk
    }

    output = dict()

    num_users = matrix_Predict.shape[0]

    for k in atK:

        local_metric_names = list(set(metric_names).intersection(local_metrics.keys()))
        results = {name: [] for name in local_metric_names}
        topK_Predict = matrix_Predict[:, :k]

        for user_index in tqdm(range(topK_Predict.shape[0])):
            vector_predict = topK_Predict[user_index]
            if len(vector_predict.nonzero()[0]) > 0:
                vector_true = matrix_Test[user_index]
                vector_true_dense = vector_true.nonzero()[1]
                hits = np.isin(vector_predict, vector_true_dense)

                if vector_true_dense.size > 0:
                    for name in local_metric_names:
                        results[name].append(local_metrics[name](vector_true_dense=vector_true_dense,
                                                                 vector_predict=vector_predict,
                                                                 hits=hits))
        results_summary = dict()
        if analytical:
            for name in local_metric_names:
                results_summary['{0}@{1}'.format(name, k)] = round(results[name],4)
        else:
            for name in local_metric_names:
                results_summary['{0}@{1}'.format(name, k)] = (round((np.average(results[name])),4),
                                                              round((1.96*np.std(results[name])/np.sqrt(num_users)),4))
        output.update(results_summary)

    global_metric_names = list(set(metric_names).intersection(global_metrics.keys()))
    results = {name: [] for name in global_metric_names}

    topK_Predict = matrix_Predict[:]

    for user_index in tqdm(range(topK_Predict.shape[0])):
        vector_predict = topK_Predict[user_index]

        if len(vector_predict.nonzero()[0]) > 0:
            vector_true = matrix_Test[user_index]
            vector_true_dense = vector_true.nonzero()[1]
            hits = np.isin(vector_predict, vector_true_dense)

            # if user_index == 1:
            #     import ipdb;
            #     ipdb.set_trace()

            if vector_true_dense.size > 0:
                for name in global_metric_names:
                    results[name].append(global_metrics[name](vector_true_dense=vector_true_dense,
                                                              vector_predict=vector_predict,
                                                              hits=hits))
    results_summary = dict()
    if analytical:
        for name in global_metric_names:
            results_summary[name] = round(results[name],4)
    else:
        for name in global_metric_names:
            results_summary[name] = (round(np.average(results[name]),4), round((1.96*np.std(results[name])/np.sqrt(num_users)),4))
    output.update(results_summary)

    return output

## Add 2 matrices

In [11]:
## Utility functions
#3906 restuarant, 3000 keyphrase, 5791 user 
def add_two_matrix(ratio, U_I_matrix,I_K_matrix, shape = (3906, 3000+5791)):
    # ratio determine Keywords/User in the matrix
    rows = []
    cols = []
    datas = []
    I_U_matrix = U_I_matrix.transpose()
    
    #for each restuarant
    for i in tqdm(range(I_K_matrix.shape[0])):
        #key phrase that this item has, column(key phrase) index
        nonzero1 = I_K_matrix[i].nonzero()
        
        #user that rated this item, column(user) index 
        nonzero2 = I_U_matrix[i].nonzero()
        
        #Trying to create a sparse matrix that stores 
        #index of restuarant for (K + U) times
        row = [i]*(len(nonzero1[1])+len(nonzero2[1]))
        
        #column index for key phrase and users that are non-zero
        col = nonzero1[1].tolist()+ nonzero2[1].tolist()
        
        
        data = [ratio]*len(nonzero1[1])+[1-ratio]*len(nonzero2[1]) # Binary representation of I-K/U matrix
        
        rows.extend(row)
        cols.extend(col)
        datas.extend(data)
    return csr_matrix( (datas,(rows,cols)), shape=shape )

def transfer_to_implicit(rating_matrix, threshold = 0):
    temp_rating_matrix = sparse.csr_matrix(rating_matrix.shape)
    temp_rating_matrix[(rating_matrix > threshold).nonzero()] = 1
    rating_matrix = temp_rating_matrix
    return rating_matrix

#### Get original dataframe out of the review datastet

In [13]:
#Getting the yelp data -> reviews, only get the data for the top frequent users & restuarants that had a history of rating > 3
df = get_yelp_df(path ='', filename=reviewJsonWithClosedRes, sampling= True)

In [14]:
df['reviewStars_userAvg'] = df['review_stars'] - df['user_avg_stars']
df.loc[df['reviewStars_userAvg'] == 0, "reviewStars_userAvg"] = 0.01
#(df['reviewStars_userAvg'] == 0.01).sum()

258860

In [82]:
#(df['reviewStars_userAvg'] == 0.01).sum()

1074

#### Get rating-UI matrix and timestepm-UI matrix

In [26]:
rating_matrix, ratingWuserAvg_matrix, timestamp_matrix = get_rating_timestamp_matrix(df)
# rating_matrix
# ratingWuserAvg_matrix

#### Split to get rtrain-UI matrix and valid and test.. item_index_matrix_train

In [27]:
rtrain, rvalid, rtest, rtrain_userAvg, rvalid_userAvg, rtest_userAvg, nonzero_index, rtime, item_idx_matrix_train,item_idx_matrix_valid, item_idx_matrix_test = time_ordered_split(rating_matrix=rating_matrix, ratingWuserAvg_matrix=ratingWuserAvg_matrix, timestamp_matrix=timestamp_matrix,
                                                                     ratio=[0.5,0.2,0.3],
                                                                     implicit=False)  

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:01<00:00, 3604.17it/s]


In [150]:
rtrain_implicit, rvalid_implicit, rtest_implicit, rtrain_userAvg_implicit, rvalid_userAvg_implicit, rtest_userAvg_implicit, nonzero_index, rtime, item_idx_matrix_train_implicit,item_idx_matrix_valid_implicit, item_idx_matrix_test_implicit = time_ordered_split(rating_matrix=rating_matrix, ratingWuserAvg_matrix=ratingWuserAvg_matrix, timestamp_matrix=timestamp_matrix,
                                                                     ratio=[0.5,0.2,0.3],
                                                                     implicit=True)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:11: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  # This is added back by InteractiveShellApp.init_path()
100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:01<00:00, 5157.58it/s]


#### Get df shrink to df_train for rtrain

In [52]:
#Get the list of row index for the training set 
lst_train = get_corpus_idx_list(df, item_idx_matrix_train)

# Get the training dataframe from the original dataframe
df_train = df.loc[lst_train]

#Resetting the index of the train data
df_train = df_train.reset_index(drop=True)

df_train.shape

100%|██████████████████████████████████████████████████████████████████████████████| 6087/6087 [02:25<00:00, 41.76it/s]


(125879, 14)

#### If using term frequency only to compute corpus and X(review vs. terms) CounterVectorizer

In [19]:
# The entire corpus
#corpus = preprocess(df_train)
# X row: df_train row, column: key words frequency 
# When building the vocabulary ignore terms that have a document frequency strictly higher than the given threshold
#cv=CountVectorizer(max_df=0.9,stop_words=stop_words, max_features=5000, ngram_range=(1,1))
#X=cv.fit_transform(corpus)

##### If using TD-IDF to compute corpus and X (business vs. terms) TfIdfVectorizer

In [20]:
from sklearn.feature_extraction.text import TfidfVectorizer

In [21]:
corpus = preprocess(df_train)

100%|████████████████████████████████████████████████████████████████████████| 125794/125794 [00:47<00:00, 2662.22it/s]


In [22]:
#Creating a dictionary to store business: review text
dict_text = {}
for i in range(len(corpus)):
    if df_train['business_num_id'][i] not in dict_text:
        dict_text[df_train['business_num_id'][i]] = corpus[i]
    else:
        temp = dict_text[df_train['business_num_id'][i]]
        temp = temp + corpus[i]
        dict_text[df_train['business_num_id'][i]] = temp

In [23]:
#Create a list for the review text, where the row dimension = total business ids
list_text = []
for key in range(0,max(list(dict_text.keys()))+1) :
    if key not in dict_text.keys():
        list_text.extend([""])
    else:
        list_text.extend([dict_text[key]])

In [24]:
#Get the X vector, where dimension is #business vs #terms
vectorizer = TfidfVectorizer(max_df=0.9,stop_words=stop_words, max_features=5000, ngram_range=(1,1))
X_cleaned = vectorizer.fit_transform(list_text).toarray()
X_cleaned_sparse = csr_matrix(X_cleaned)

## User-rating KNN

### 1. With ratings that subtracts user average rating, cosine similarity

In [123]:
#UU similarity, using cosine similarity
similarity1 = train(rtrain)
#get a user-item matrix  UI prediction
#Predict using UI matrix with ratings in it 
user_item_prediction_score1 = predict(rtrain_userAvg, 90, similarity1, item_similarity_en= False)
user_item_predict1 = prediction(user_item_prediction_score1, 50, rtrain_userAvg)

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:01<00:00, 4498.73it/s]


In [124]:
user_item_prediction_score1.shape

(6085, 4000)

In [84]:
user_item_res1 = evaluate(user_item_predict1, rvalid_userAvg)

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 9172.32it/s]


In [85]:
#user_item_res1.get('MAP@10')[0]
user_item_res1

{'MAP@5': (0.0478, 0.0031),
 'MAP@10': (0.0433, 0.0023),
 'MAP@15': (0.0403, 0.0019),
 'MAP@20': (0.038, 0.0017),
 'MAP@50': (0.0305, 0.0011)}

## Implicit

In [151]:
#UU similarity, using cosine similarity
similarity1 = train(rtrain_implicit)
#get a user-item matrix  UI prediction
#Predict using UI matrix with ratings in it 
user_item_prediction_score1 = predict(rtrain_implicit, 90, similarity1, item_similarity_en= False)
user_item_predict1 = prediction(user_item_prediction_score1, 50, rtrain_implicit)
user_item_res1 = evaluate(user_item_predict1, rvalid_implicit)
user_item_res1

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 9117.15it/s]


{'MAP@5': (0.0536, 0.0033),
 'MAP@10': (0.0497, 0.0025),
 'MAP@15': (0.047, 0.002),
 'MAP@20': (0.0448, 0.0018),
 'MAP@50': (0.0375, 0.0012)}

In [152]:
print(rvalid_implicit.sum())

39740.0


### 2. With ratings that subtracts user average rating, pearson correlation

In [30]:
# #UU similarity, using cosine similarity
# similarity2 = train(rtrain_userAvg)
# #get a user-item matrix  UI prediction
# #Predict using UI matrix with ratings in it 
# user_item_prediction_score2 = predict(rtrain_userAvg, 100, similarity2, item_similarity_en= False)
# user_item_predict2 = prediction(user_item_prediction_score2, 50, rtrain_userAvg)
# user_item_res2 = evaluate(user_item_predict2, rvalid_userAvg)
# user_item_res2

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:01<00:00, 4412.00it/s]


### 3. With raw ratings, cosinesimilarity

In [86]:
#UU similarity
similarity3 = train(rtrain)
#get a user-item matrix  UI prediction
#Predict using UI matrix with ratings in it 
user_item_prediction_score3 = predict(rtrain, 90, similarity3, item_similarity_en= False)
user_item_predict3 = prediction(user_item_prediction_score3, 50, rtrain)
#Check user item prediction score
user_item_res3 = evaluate(user_item_predict3, rvalid)

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 8918.03it/s]


In [87]:
user_item_res3

{'MAP@5': (0.0564, 0.0034),
 'MAP@10': (0.0518, 0.0025),
 'MAP@15': (0.0491, 0.0021),
 'MAP@20': (0.047, 0.0019),
 'MAP@50': (0.0391, 0.0012)}

## Item Base KNN using TF-IDF

In [48]:
IK_MATRIX = X_cleaned_sparse

In [49]:
I_I_similarity = train(IK_MATRIX)
item_based_prediction_score4 = predict(rtrain, 10, I_I_similarity, item_similarity_en= True)
#for each restuarant top50 users 
item_based_predict4 = prediction(item_based_prediction_score4, 50, rtrain)

100%|████████████████████████████████████████████████████████████████████████████| 6088/6088 [00:01<00:00, 3433.24it/s]


In [51]:
item_based_res_TFIDF = evaluate(item_based_predict4, rvalid)

100%|████████████████████████████████████████████████████████████████████████████| 6088/6088 [00:00<00:00, 6098.03it/s]


In [52]:
item_based_res_TFIDF

{'MAP@5': (0.025720090045571842, 0.0023778194577824324),
 'Recall@5': (0.016655483869688705, 0.0017397463525098502),
 'Precision@5': (0.022467468291879424, 0.0017674622991041998),
 'MAP@10': (0.022609687481207827, 0.0017360525467602446),
 'Recall@10': (0.027194281753721176, 0.002222645640702759),
 'Precision@10': (0.018283643551309504, 0.0011753292576658),
 'MAP@15': (0.020781676396896296, 0.00142907310519044),
 'Recall@15': (0.036517627228885796, 0.0025924958256981607),
 'Precision@15': (0.0165266567836161, 0.0009373298279886963),
 'MAP@20': (0.019509841866004404, 0.0012405775324402586),
 'Recall@20': (0.044301527297699116, 0.002866338517957658),
 'Precision@20': (0.015112831493987811, 0.0007917345810550951),
 'MAP@50': (0.015555777760667203, 0.0007797415508435789),
 'Recall@50': (0.08003652685068291, 0.003781329780486565),
 'Precision@50': (0.011391862955032118, 0.0004649805491420753),
 'R-Precision': (0.019076629311042183, 0.0015214914170442837),
 'NDCG': (0.04568113642606309, 0.002

## Try combining different similarity scores

In [179]:
#Get a UI matrix if it's not item_similarity based or else IU
def predictUU(matrix_train, k, similarity1, similarity2=None, similarity3=None, similarity4=None, weight1=None, weight2=None, weight3=None, weight4=None, chooseWeigthMethod = None, item_similarity_en = False):
    prediction_scores = []
    
    #inverse to IU matrix
    if item_similarity_en:
        matrix_train = matrix_train.transpose()
        
    #for each user or item, depends UI or IU 
    for user_index in tqdm(range(matrix_train.shape[0])):
    #for user_index in tqdm(range(1)):
        
        numberSimilarMatrix = 0
        # Get user u's prediction scores for all items 
        #Get prediction/similarity score for each user 1*num or user or num of items
        vector_u1 = similarity1[user_index]
        numberSimilarMatrix += 1
        
        if similarity2 is not None:
            vector_u2 = similarity2[user_index]
            numberSimilarMatrix += 1
        else:
            vector_u2 = [0]*len(vector_u1)
            
        if similarity3 is not None:
            vector_u3 = similarity3[user_index]
            numberSimilarMatrix += 1
        else:
            vector_u3 = [0]*len(vector_u1)
            
        if similarity4 is not None:
            vector_u4 = similarity4[user_index]
            numberSimilarMatrix += 1
        else:
            vector_u4 = [0]*len(vector_u1)
        
        vector_u = vector_u1.copy()
            
        #If we are choosing the max, min, or avg or similarity scores
        if chooseWeigthMethod is not None:
            #loop through the user index 
            for item_index in tqdm(range(matrix_train.shape[0])):

                if chooseWeigthMethod == 'max':
                    vector_u[item_index] = max(vector_u1[item_index], vector_u2[item_index], vector_u3[item_index],vector_u4[item_index])
                elif chooseWeigthMethod == 'min':
                    vector_u[item_index] = min(vector_u1[item_index], vector_u2[item_index], vector_u3[item_index],vector_u4[item_index])
                elif chooseWeigthMethod == 'average':
                    vector_u[item_index] = (vector_u1[item_index]+vector_u2[item_index]+vector_u3[item_index]+vector_u4[item_index])/(numberSimilarMatrix)
        
        similar_users = vector_u.argsort()[::-1][1:k+1]
        
        # Get neighbors similarity weights and ratings
        #similar_users_weights = similarity1[user_index][similar_users]
        similar_users_weights = vector_u[similar_users]
        
        #similar_users_weights_sum = np.sum(similar_users_weights)
        #print(similar_users_weights.shape)
        #shape: num of res * k
        similar_users_ratings = matrix_train[similar_users].toarray()
              
        prediction_scores_u = similar_users_ratings * similar_users_weights[:, np.newaxis]
        #print(prediction_scores_u)
        
        prediction_scores.append(np.sum(prediction_scores_u, axis=0))
        
    res = np.array(prediction_scores)
    
    if item_similarity_en:
        res = res.transpose()
    return res
    #return vector_u

In [194]:
#UU similarity, using cosine similarity
similarity1 = train(rtrain)
#similarity2 = train(rtrain_userAvg)
similarity2 = None
#similarity3 =train(userVisitMatrix)
similarity3 = None
similarity4 = train(rtrain_implicit)
#similarity4 = None
weight1 = None
weight2=None
weight3=None
#vectorU = predictUU(rtrain_userAvg, 90, similarity1, similarity2, similarity3, weight1, weight2, weight3, item_similarity_en= False)
user_item_prediction_score1 = predictUU(rtrain, 90, similarity1, similarity2, similarity3, similarity4, weight1, weight2, weight3, chooseWeigthMethod = 'average', item_similarity_en= False)
user_item_predict1 = prediction(user_item_prediction_score1, 50, rtrain)
user_item_res1 = evaluate(user_item_predict1, rvalid)


  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304817.15it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305079.49it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304657.05it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290541.64it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304598.88it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

  1%|▍                                                                               | 33/6085 [00:00<02:33, 39.47it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305061.26it/s]

  0%|                           

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305079.49it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

  1%|▊                                                                               | 62/6085 [00:01<02:29, 40.21it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305057.61it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290538.33it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|███████████████████████████

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

  2%|█▏                                                                              | 92/6085 [00:02<02:29, 40.21it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304657.05it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305064.90it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305064.90it/s]

  0%|                           

  2%|█▌                                                                             | 122/6085 [00:03<02:30, 39.61it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 321132.67it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305075.84it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305064.90it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|███████████████████████████

...

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304638.87it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304635.23it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

 99%|████████████████████████████████████████████████████████████████████████████▊ | 5994/6085 [02:28<00:02, 40.31it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290538.33it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|███████████████████████████

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304606.15it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

 99%|█████████████████████████████████████████████████████████████████████████████▏| 6024/6085 [02:29<00:01, 40.74it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 304726.16it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290551.56it/s]

  0%|                           

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290541.64it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

 99%|█████████████████████████████████████████████████████████████████████████████▌| 6054/6085 [02:30<00:00, 40.29it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 305079.49it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|██████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 290538.33it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|███████████████████████████

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

100%|█████████████████████████████████████████████████████████████████████████████▉| 6084/6085 [02:31<00:00, 40.72it/s]

  0%|                                                                                         | 0/6085 [00:00<?, ?it/s]

 68%|████████████████████████████████████████████████████                        | 4168/6085 [00:00<00:00, 6914.88it/s]


100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 9052.36it/s]

In [195]:
user_item_res1

{'MAP@5': (0.0844, 0.0042),
 'MAP@10': (0.073, 0.0031),
 'MAP@15': (0.0664, 0.0025),
 'MAP@20': (0.0617, 0.0022),
 'MAP@50': (0.0477, 0.0014)}

In [192]:
user_item_res1    #1,4 average with userVisitMatrix, rvalid 

{'MAP@5': (0.0797, 0.0041),
 'MAP@10': (0.069, 0.003),
 'MAP@15': (0.063, 0.0024),
 'MAP@20': (0.0588, 0.0021),
 'MAP@50': (0.0458, 0.0013)}

In [190]:
user_item_res1

{'MAP@5': (0.0572, 0.0035),
 'MAP@10': (0.0498, 0.0025),
 'MAP@15': (0.0455, 0.0021),
 'MAP@20': (0.0425, 0.0018),
 'MAP@50': (0.0331, 0.0011)}

In [188]:
user_item_res1 #average 1,4 similarity matrices

{'MAP@5': (0.0709, 0.0039),
 'MAP@10': (0.0612, 0.0028),
 'MAP@15': (0.0558, 0.0023),
 'MAP@20': (0.052, 0.002),
 'MAP@50': (0.0402, 0.0013)}

In [186]:
user_item_res1 #average 1,2,4 similarity matrices

{'MAP@5': (0.061, 0.0036),
 'MAP@10': (0.0545, 0.0026),
 'MAP@15': (0.0504, 0.0022),
 'MAP@20': (0.0474, 0.0019),
 'MAP@50': (0.0379, 0.0012)}

In [183]:
user_item_res1    #average 1-2 similarity matrices

{'MAP@5': (0.0447, 0.0031),
 'MAP@10': (0.0421, 0.0023),
 'MAP@15': (0.0402, 0.0019),
 'MAP@20': (0.0386, 0.0017),
 'MAP@50': (0.0324, 0.0011)}

In [181]:
user_item_res1   #average 3 1-3similarity matrices

{'MAP@5': (0.0469, 0.0031),
 'MAP@10': (0.0442, 0.0023),
 'MAP@15': (0.0421, 0.002),
 'MAP@20': (0.0403, 0.0017),
 'MAP@50': (0.0335, 0.0011)}

In [173]:
user_item_res1  #average 4, 1-4similarity matrices

{'MAP@5': (0.0577, 0.0035),
 'MAP@10': (0.0522, 0.0026),
 'MAP@15': (0.0486, 0.0021),
 'MAP@20': (0.0459, 0.0019),
 'MAP@50': (0.037, 0.0012)}

In [160]:
user_item_res1   #min

{'MAP@5': (0.0455, 0.0031),
 'MAP@10': (0.0425, 0.0023),
 'MAP@15': (0.0403, 0.0019),
 'MAP@20': (0.0384, 0.0017),
 'MAP@50': (0.032, 0.0011)}

In [155]:
user_item_res1 #max

{'MAP@5': (0.0738, 0.004),
 'MAP@10': (0.0635, 0.0029),
 'MAP@15': (0.0576, 0.0023),
 'MAP@20': (0.0534, 0.002),
 'MAP@50': (0.041, 0.0012)}

In [132]:
user_item_res1  #rtrain

{'MAP@5': (0.0505, 0.0032),
 'MAP@10': (0.0468, 0.0024),
 'MAP@15': (0.0443, 0.002),
 'MAP@20': (0.0422, 0.0018),
 'MAP@50': (0.0349, 0.0012)}

In [130]:
user_item_res1 #rtrain_userAvg

{'MAP@5': (0.0483, 0.0031),
 'MAP@10': (0.0433, 0.0023),
 'MAP@15': (0.0401, 0.0019),
 'MAP@20': (0.0377, 0.0017),
 'MAP@50': (0.0301, 0.0011)}

In [122]:
user_item_prediction_score1.shape

(1, 4000)

In [ ]:
[3764   36  896 5156 5737  618 2345   11 1706 1554  726  627 5821 3348
  243 1571 1247 5209  203 4856 3754  544 5417 3849 2411 1763  274 5211
   91 2558 4208 4063 4712 3520  457 2900  387 2455 1178 3024 1342 6014
 2823 5848 4691 5099 5109 5545 3987 6069 5794 5572   77 3180 3266 5039
 5904 2325 3628  493 5735   27 4797 4813 3128 5337 4845 3907 3544 2128
  320  134 1985 3470 5944 3188 2438 4850 2630 3912 1245 1674 5986 2360
 5094 3670 5902 1491 3997 3856]

In [ ]:
[3026 4208 5069 5507 1571 3529  544 3090 2538 4797 3527 1558 6079 5736
   13 5209 5363 1866 3640 5684 1062 5213 5757 5417 5986 1466 5902 3109
 4096  464  493  629 3912 3814 1268 3552 2438 5109 1207 4504 5634 4870
 5229  320 4354  785 3167 2416 3128 4540 5457 5420 1241 1674 4850 5140
   15  457  710 1245  942 5147 5164 4314 4346 3648 3180 3103 3189 1357
 4917 3987 5571 2906  210 2489  901 2293 5737  879 2558  564 4310 2119
 5521 5059 2376 3856 1967 4094]

In [75]:
for number in rtrain_userAvg:
    print(number)

  (0, 0)	0.08
  (0, 677)	1.08
  (0, 1074)	1.08
  (0, 1344)	0.08
  (0, 1345)	1.08
  (0, 1711)	0.08
  (0, 1742)	1.08
  (0, 2611)	-2.92
  (0, 2691)	-2.92
  (0, 2787)	-2.92
  (0, 2799)	0.08
  (0, 2801)	1.08
  (0, 3084)	0.08
  (0, 3466)	1.08
  (0, 3514)	1.08
  (0, 3592)	0.08
  (0, 3900)	0.08
  (0, 3927)	-2.92
  (0, 54)	-1.21
  (0, 222)	0.79
  (0, 223)	0.79
  (0, 441)	-0.21
  (0, 586)	0.79
  (0, 705)	0.79
  (0, 772)	-0.21
  (0, 795)	-0.21
  (0, 906)	-0.21
  (0, 1146)	-0.21
  (0, 1255)	-0.21
  (0, 1367)	-0.21
  (0, 1475)	0.79
  (0, 2157)	-1.21
  (0, 2383)	0.79
  (0, 2613)	-0.21
  (0, 2882)	0.79
  (0, 2892)	-0.21
  (0, 3001)	0.79
  (0, 3149)	0.79
  (0, 3170)	-0.21
  (0, 3224)	-1.21
  (0, 3267)	-0.21
  (0, 3458)	0.79
  (0, 3641)	0.79
  (0, 166)	0.31
  (0, 187)	-0.69
  (0, 282)	1.31
  (0, 318)	0.31
  (0, 464)	0.31
  (0, 547)	0.31
  (0, 566)	1.31
  (0, 881)	0.31
  (0, 1589)	0.31
  (0, 1796)	0.31
  (0, 1846)	-1.69
  (0, 2000)	-0.69
  (0, 2247)	0.31
  (0, 2330)	0.31
  (0, 2372)	0.31
  (0, 2814)	-2.

  (0, 3522)	0.21
  (0, 1385)	0.73
  (0, 1779)	-1.27
  (0, 3198)	0.73
  (0, 3650)	0.73
  (0, 131)	-1.89
  (0, 390)	0.11
  (0, 646)	1.11
  (0, 679)	1.11
  (0, 901)	0.11
  (0, 909)	-0.89
  (0, 1084)	-1.89
  (0, 2584)	0.11
  (0, 2711)	1.11
  (0, 3814)	1.11
  (0, 10)	0.12
  (0, 113)	0.12
  (0, 310)	0.12
  (0, 353)	1.12
  (0, 357)	-1.88
  (0, 431)	-0.88
  (0, 540)	-0.88
  (0, 830)	-0.88
  (0, 969)	1.12
  (0, 1109)	0.12
  (0, 1325)	0.12
  (0, 1529)	-0.88
  (0, 1839)	0.12
  (0, 1876)	0.12
  (0, 2123)	0.12
  (0, 2234)	0.12
  (0, 2323)	-1.88
  (0, 2573)	-1.88
  (0, 2798)	-0.88
  (0, 3174)	0.12
  (0, 3681)	-0.88
  (0, 3941)	-1.88
  (0, 312)	1.29
  (0, 408)	1.29
  (0, 511)	1.29
  (0, 552)	1.29
  (0, 2110)	1.29
  (0, 2154)	1.29
  (0, 2344)	1.29
  (0, 2575)	1.29
  (0, 2614)	1.29
  (0, 2815)	1.29
  (0, 3288)	1.29
  (0, 3515)	1.29
  (0, 3544)	-2.71
  (0, 3673)	1.29
  (0, 3813)	1.29
  (0, 3927)	1.29
  (0, 244)	1.33
  (0, 282)	1.33
  (0, 286)	0.33
  (0, 472)	0.33
  (0, 497)	0.33
  (0, 821)	-0.67
  (0, 8

  (0, 3843)	-0.36
  (0, 113)	-0.68
  (0, 414)	-0.68
  (0, 536)	0.32
  (0, 790)	-0.68
  (0, 898)	-1.68
  (0, 1031)	0.32
  (0, 1251)	1.32
  (0, 1526)	-0.68
  (0, 1734)	0.32
  (0, 2035)	1.32
  (0, 2123)	0.32
  (0, 2323)	0.32
  (0, 2353)	-0.68
  (0, 2590)	0.32
  (0, 2884)	0.32
  (0, 3303)	0.32
  (0, 3404)	1.32
  (0, 3484)	-0.68
  (0, 3654)	1.32
  (0, 3681)	-0.68
  (0, 3832)	1.32
  (0, 231)	0.02
  (0, 279)	1.02
  (0, 671)	0.02
  (0, 835)	1.02
  (0, 1030)	1.02
  (0, 1314)	-0.98
  (0, 1358)	0.02
  (0, 1559)	-0.98
  (0, 2537)	1.02
  (0, 2625)	0.02
  (0, 2749)	0.02
  (0, 2770)	0.02
  (0, 3099)	1.02
  (0, 3177)	0.02
  (0, 3182)	0.02
  (0, 3866)	1.02
  (0, 352)	-0.1
  (0, 361)	-0.1
  (0, 453)	-0.1
  (0, 503)	0.9
  (0, 734)	0.9
  (0, 875)	-0.1
  (0, 1013)	-1.1
  (0, 1155)	0.9
  (0, 1176)	0.9
  (0, 1409)	0.9
  (0, 1501)	0.9
  (0, 1698)	-0.1
  (0, 1711)	0.9
  (0, 1814)	0.9
  (0, 2146)	0.9
  (0, 2247)	0.9
  (0, 2456)	0.9
  (0, 2813)	0.9
  (0, 2948)	-0.1
  (0, 2958)	0.9
  (0, 3079)	-0.1
  (0, 3120)	0.

  (0, 3906)	1.24
  (0, 100)	0.55
  (0, 660)	0.55
  (0, 904)	1.55
  (0, 1111)	0.55
  (0, 1182)	0.55
  (0, 1405)	-1.45
  (0, 1503)	-0.45
  (0, 1823)	-0.45
  (0, 2076)	0.55
  (0, 2262)	-1.45
  (0, 2671)	0.55
  (0, 2759)	-0.45
  (0, 2795)	0.55
  (0, 2924)	1.55
  (0, 3106)	0.55
  (0, 3211)	1.55
  (0, 3316)	-0.45
  (0, 3505)	0.55
  (0, 3618)	1.55
  (0, 3621)	1.55
  (0, 3657)	0.55
  (0, 3741)	-1.45
  (0, 3904)	-0.45
  (0, 102)	0.29
  (0, 394)	-2.71
  (0, 903)	-2.71
  (0, 933)	0.29
  (0, 1023)	0.29
  (0, 1108)	0.29
  (0, 1142)	0.29
  (0, 1155)	1.29
  (0, 1224)	1.29
  (0, 1321)	1.29
  (0, 1863)	0.29
  (0, 2065)	-1.71
  (0, 2132)	0.29
  (0, 2177)	1.29
  (0, 2280)	0.29
  (0, 2553)	0.29
  (0, 2646)	-2.71
  (0, 2655)	-0.71
  (0, 2787)	-1.71
  (0, 3016)	0.29
  (0, 3156)	0.29
  (0, 3329)	1.29
  (0, 3334)	-0.71
  (0, 3553)	-0.71
  (0, 3769)	1.29
  (0, 3801)	-1.71
  (0, 3829)	1.29
  (0, 3891)	0.29
  (0, 2)	1.29
  (0, 6)	0.29
  (0, 142)	-0.71
  (0, 167)	0.29
  (0, 268)	0.29
  (0, 330)	-0.71
  (0, 383)	0

  (0, 3977)	1.25
  (0, 1054)	1.28
  (0, 18)	1.24
  (0, 107)	1.24
  (0, 305)	0.24
  (0, 504)	-0.76
  (0, 528)	0.24
  (0, 717)	0.24
  (0, 782)	0.24
  (0, 883)	1.24
  (0, 979)	-0.76
  (0, 1112)	0.24
  (0, 1153)	0.24
  (0, 1275)	-0.76
  (0, 1369)	-0.76
  (0, 1595)	1.24
  (0, 1901)	1.24
  (0, 2208)	0.24
  (0, 2268)	0.24
  (0, 2329)	-0.76
  (0, 2365)	0.24
  (0, 2557)	0.24
  (0, 2928)	-0.76
  (0, 2965)	0.24
  (0, 3038)	0.24
  (0, 3319)	-0.76
  (0, 3655)	0.24
  (0, 3708)	1.24
  (0, 3742)	-0.76
  (0, 3877)	0.24
  (0, 3892)	0.24
  (0, 3925)	0.24
  (0, 3949)	0.24
  (0, 190)	-1.01
  (0, 205)	0.99
  (0, 319)	0.99
  (0, 1087)	-2.01
  (0, 1521)	0.99
  (0, 1568)	0.99
  (0, 1749)	-0.01
  (0, 1940)	0.99
  (0, 2042)	0.99
  (0, 2496)	0.99
  (0, 3202)	-0.01
  (0, 3731)	-0.01
  (0, 3776)	-0.01
  (0, 3853)	0.99
  (0, 439)	-2.26
  (0, 726)	0.74
  (0, 1163)	-0.26
  (0, 1224)	0.74
  (0, 1405)	0.74
  (0, 1416)	-1.26
  (0, 2214)	0.74
  (0, 2571)	-0.26
  (0, 2708)	-0.26
  (0, 2938)	-0.26
  (0, 3031)	-0.26
  (0, 31

...

  (0, 3998)	0.53
  (0, 92)	1.29
  (0, 740)	0.29
  (0, 807)	-0.71
  (0, 921)	0.29
  (0, 1099)	-0.71
  (0, 1157)	0.29
  (0, 1231)	0.29
  (0, 1238)	-0.71
  (0, 1618)	0.29
  (0, 1705)	0.29
  (0, 2034)	1.29
  (0, 2078)	1.29
  (0, 2327)	0.29
  (0, 2371)	-0.71
  (0, 2753)	0.29
  (0, 2965)	0.29
  (0, 3254)	0.29
  (0, 3313)	0.29
  (0, 3649)	0.29
  (0, 327)	0.29
  (0, 1260)	0.29
  (0, 1318)	-0.71
  (0, 2768)	-0.71
  (0, 3152)	-0.71
  (0, 3372)	0.29
  (0, 3754)	0.29
  (0, 210)	0.08
  (0, 584)	-0.92
  (0, 893)	0.08
  (0, 1083)	-0.92
  (0, 1471)	-0.92
  (0, 1579)	0.08
  (0, 1650)	0.08
  (0, 1791)	-0.92
  (0, 2464)	1.08
  (0, 2593)	0.08
  (0, 2667)	0.08
  (0, 2987)	0.08
  (0, 3449)	1.08
  (0, 3537)	0.08
  (0, 3675)	0.08
  (0, 101)	-0.02
  (0, 121)	-1.02
  (0, 182)	-0.02
  (0, 242)	-0.02
  (0, 268)	-0.02
  (0, 286)	-0.02
  (0, 353)	-0.02
  (0, 381)	-0.02
  (0, 591)	-3.02
  (0, 771)	-0.02
  (0, 897)	-1.02
  (0, 937)	-1.02
  (0, 995)	-0.02
  (0, 1012)	-1.02
  (0, 1037)	-0.02
  (0, 1042)	-0.02
  (0, 120

  (0, 3774)	-1.1
  (0, 79)	1.29
  (0, 120)	1.29
  (0, 201)	1.29
  (0, 238)	1.29
  (0, 262)	1.29
  (0, 282)	0.29
  (0, 306)	0.29
  (0, 318)	1.29
  (0, 353)	0.29
  (0, 627)	0.29
  (0, 653)	0.29
  (0, 656)	-0.71
  (0, 679)	1.29
  (0, 720)	-0.71
  (0, 745)	-0.71
  (0, 833)	-0.71
  (0, 952)	0.29
  (0, 956)	-1.71
  (0, 981)	0.29
  (0, 1010)	0.29
  (0, 1021)	0.29
  (0, 1115)	0.29
  (0, 1291)	1.29
  (0, 1345)	-2.71
  (0, 1533)	1.29
  :	:
  (0, 2359)	0.29
  (0, 2520)	0.29
  (0, 2621)	0.29
  (0, 2653)	0.29
  (0, 2787)	0.29
  (0, 2799)	0.29
  (0, 2873)	-0.71
  (0, 2948)	-2.71
  (0, 3016)	0.29
  (0, 3032)	-0.71
  (0, 3085)	1.29
  (0, 3103)	0.29
  (0, 3160)	0.29
  (0, 3200)	1.29
  (0, 3345)	0.29
  (0, 3397)	0.29
  (0, 3425)	0.29
  (0, 3468)	1.29
  (0, 3504)	-0.71
  (0, 3620)	-2.71
  (0, 3702)	-0.71
  (0, 3749)	1.29
  (0, 3768)	0.29
  (0, 3833)	1.29
  (0, 3976)	-1.71
  (0, 65)	1.04
  (0, 145)	1.04
  (0, 239)	-0.96
  (0, 455)	-2.96
  (0, 772)	-2.96
  (0, 1283)	1.04
  (0, 2152)	0.04
  (0, 2185)	-1.96


  (0, 3958)	-0.11
  (0, 59)	0.57
  (0, 351)	0.57
  (0, 538)	0.57
  (0, 636)	-0.43
  (0, 785)	-1.43
  (0, 930)	-0.43
  (0, 1224)	-0.43
  (0, 1227)	-0.43
  (0, 1264)	0.57
  (0, 1407)	0.57
  (0, 1422)	0.57
  (0, 2216)	-0.43
  (0, 2312)	0.57
  (0, 2327)	0.57
  (0, 2718)	-0.43
  (0, 2844)	0.57
  (0, 3223)	-0.43
  (0, 3298)	-0.43
  (0, 3538)	0.57
  (0, 3699)	0.57
  (0, 3905)	-0.43
  (0, 50)	0.18
  (0, 109)	0.18
  (0, 903)	0.18
  (0, 977)	0.18
  (0, 1019)	0.18
  (0, 1565)	-0.82
  (0, 1624)	-0.82
  (0, 2113)	0.18
  (0, 2595)	0.18
  (0, 2753)	1.18
  (0, 3046)	1.18
  (0, 3417)	0.18
  (0, 3741)	-0.82
  (0, 3823)	-0.82
  (0, 3992)	0.18
  (0, 83)	0.12
  (0, 391)	1.12
  (0, 1104)	0.12
  (0, 1666)	1.12
  (0, 1936)	-1.88
  (0, 2203)	-1.88
  (0, 2562)	0.12
  (0, 3260)	0.12
  (0, 3640)	0.12
  (0, 2)	0.36
  (0, 62)	0.36
  (0, 253)	1.36
  (0, 344)	-0.64
  (0, 393)	0.36
  (0, 400)	0.36
  (0, 488)	-0.64
  (0, 596)	-0.64
  (0, 600)	0.36
  (0, 604)	0.36
  (0, 649)	0.36
  (0, 753)	-0.64
  (0, 776)	0.36
  (0, 7

  (0, 2854)	-1.74
  (0, 85)	-0.14
  (0, 517)	0.86
  (0, 716)	-0.14
  (0, 1094)	0.86
  (0, 1111)	-0.14
  (0, 1304)	0.86
  (0, 1486)	-1.14
  (0, 1515)	0.86
  (0, 1559)	-0.14
  (0, 1610)	0.86
  (0, 1624)	-0.14
  (0, 1758)	0.86
  (0, 1784)	0.86
  (0, 2328)	0.86
  (0, 2412)	-0.14
  (0, 2488)	-0.14
  (0, 2924)	-0.14
  (0, 2979)	0.86
  (0, 2994)	0.86
  (0, 3151)	-0.14
  (0, 3202)	0.86
  (0, 3324)	0.86
  (0, 3378)	-0.14
  (0, 3460)	0.86
  (0, 3505)	-0.14
  (0, 3538)	0.86
  (0, 3574)	-0.14
  (0, 3722)	-0.14
  (0, 3886)	-0.14
  (0, 3907)	-0.14
  (0, 3929)	-0.14
  (0, 12)	-2.27
  (0, 125)	0.73
  (0, 152)	0.73
  (0, 234)	0.73
  (0, 548)	0.73
  (0, 679)	-0.27
  (0, 768)	0.73
  (0, 833)	-1.27
  (0, 963)	-0.27
  (0, 981)	-0.27
  (0, 1001)	-0.27
  (0, 1244)	0.73
  (0, 1295)	-1.27
  (0, 1580)	0.73
  (0, 1693)	-0.27
  (0, 1988)	0.73
  (0, 1994)	0.73
  (0, 2082)	0.73
  (0, 2202)	-0.27
  (0, 2223)	0.73
  (0, 2661)	-0.27
  (0, 2720)	-2.27
  (0, 2740)	0.73
  (0, 2745)	0.73
  (0, 2836)	0.73
  (0, 2851)	-0.27

  (0, 3913)	-2.14
  (0, 240)	0.83
  (0, 369)	0.83
  (0, 494)	-3.17
  (0, 714)	0.83
  (0, 726)	-0.17
  (0, 859)	0.83
  (0, 1292)	-0.17
  (0, 1758)	0.83
  (0, 2105)	-0.17
  (0, 2533)	-0.17
  (0, 3161)	-0.17
  (0, 3202)	-0.17
  (0, 3310)	0.83
  (0, 3350)	0.83
  (0, 3369)	0.83
  (0, 3405)	-0.17
  (0, 3538)	0.83
  (0, 3949)	-0.17
  (0, 59)	-1.14
  (0, 102)	0.86
  (0, 278)	-2.14
  (0, 308)	-0.14
  (0, 401)	-2.14
  (0, 533)	-0.14
  (0, 591)	-0.14
  (0, 1013)	0.86
  (0, 1098)	0.86
  (0, 1119)	-3.14
  (0, 1203)	-2.14
  (0, 1259)	-1.14
  (0, 1599)	-1.14
  (0, 1958)	-3.14
  (0, 2066)	-0.14
  (0, 2309)	-0.14
  (0, 2330)	-0.14
  (0, 2341)	0.86
  (0, 2380)	0.86
  (0, 2575)	-1.14
  (0, 2861)	-0.14
  (0, 3004)	-1.14
  (0, 3124)	0.86
  (0, 3183)	0.86
  (0, 3209)	-2.14
  (0, 3709)	0.86
  (0, 3835)	-0.14
  (0, 3917)	0.86
  (0, 3989)	-0.14
  (0, 24)	-0.19
  (0, 695)	0.81
  (0, 800)	-0.19
  (0, 1348)	0.81
  (0, 1438)	-0.19
  (0, 1859)	0.81
  (0, 2477)	0.81
  (0, 2702)	-0.19
  (0, 40)	-0.01
  (0, 49)	-0.01


In [83]:
rtrain_userAvg[0][0].toarray()

array([[0.08, 0.  , 0.  , ..., 0.  , 0.  , 0.  ]], dtype=float32)

In [81]:
rtrain_userAvg.shape

(6085, 4000)

In [86]:
def getImplicitMatrix(sparseMatrix, threashold=0):
    temp_matrix = sparse.csr_matrix(sparseMatrix.shape)
    temp_matrix[(sparseMatrix > threashold).nonzero()] = 1
    return temp_matrix

In [87]:
userVisitMatrix = getImplicitMatrix(rtrain)

C:\ProgramData\Anaconda3\lib\site-packages\ipykernel_launcher.py:3: SparseEfficiencyWarning: Changing the sparsity structure of a csr_matrix is expensive. lil_matrix is more efficient.
  This is separate from the ipykernel package so we can avoid doing imports until


In [157]:
#UU similarity
similarity3 = train(userVisitMatrix)
#get a user-item matrix  UI prediction
#Predict using UI matrix with ratings in it 
user_item_prediction_score3 = predict(userVisitMatrix, 90, similarity3, item_similarity_en= False)
user_item_predict3 = prediction(user_item_prediction_score3, 50, userVisitMatrix)
#Check user item prediction score
user_item_res3 = evaluate(user_item_predict3, rvalid)

100%|████████████████████████████████████████████████████████████████████████████| 6085/6085 [00:00<00:00, 9092.89it/s]


In [158]:
user_item_res3

{'MAP@5': (0.056, 0.0034),
 'MAP@10': (0.0521, 0.0025),
 'MAP@15': (0.0493, 0.0021),
 'MAP@20': (0.0471, 0.0019),
 'MAP@50': (0.0393, 0.0012)}

In [90]:
rtrain[0].toarray()

array([[4., 0., 0., ..., 0., 0., 0.]], dtype=float32)

In [101]:
for user_index in tqdm(range(2)):
    print(user_index)

  0%|                                                                                            | 0/2 [00:00<?, ?it/s]

0
1


100%|██████████████████████████████████████████████████████████████████████████████████| 2/2 [00:00<00:00, 2006.36it/s]


In [118]:
userVisitMatrix.shape

(6085, 4000)

In [119]:
rtrain.shape

(6085, 4000)

In [156]:
max(5,8,9,10)

10

In [164]:
stats.mean([1,1,1,1])

1

In [185]:
max([5,10,2], [10,5,9], [2,5,13])

[10, 5, 9]